In [1]:
import os
import angr
import monkeyhex # this will format numerical results in hexadecimal

filePath = 'gitfm'
proj = angr.Project(filePath)





WARNING  | 2023-02-26 17:39:42,967 | cle.loader     | The main binary is a position-independent executable. It is being loaded with a base address of 0x400000.


In [2]:
print(proj.loader,'\n\n')

print("Shared Objects:")
for so in (proj.loader.shared_objects):
    print(so)
print()
    
print(proj.arch)
    
print('min_addr',proj.loader.min_addr)

print('max_addr',proj.loader.max_addr)


print('main_object',proj.loader.main_object)  # we've loaded several binaries into this project. Here's the main one!


print('does this binary have an executable stack?: ',proj.loader.main_object.execstack)  # sample query: does this binary have an executable stack?

print('is this binary position-independent?',proj.loader.main_object.pic)  # sample query: is this binary position-independent?



<Loaded gitfm, maps [0x400000:0xc07fff]> 


Shared Objects:
gitfm
libtinfo.so.6
libc.so.6
ld-linux-x86-64.so.2
extern-address space
cle##tls

<Arch AMD64 (LE)>
min_addr 4194304
max_addr 12615679
main_object <ELF Object gitfm, maps [0x400000:0x42bc87]>
does this binary have an executable stack?:  False
is this binary position-independent? True


In [3]:
#taken inspiration form angr documentaion 

obj = proj.loader.main_object


print('# The entry point of the object',obj.entry)




print("Retrieve this ELF's segments and sections")

for segment in obj.segments:
    print('segment regions : ',segment)
print('\n\n')



for section in obj.sections:
    print("Section Regions: ",section)

            
# # You can get an individual segment or section by an address it contains:
print(" You can get an individual segment  by an address it contains:")
print('find_segment_containing(obj.entry)',obj.find_segment_containing(obj.entry))



print('\n')
print(" You can get an individual section by an address it contains:")

print("obj.find_section_containing(obj.entry)",obj.find_section_containing(obj.entry))





# The entry point of the object 4224128
Retrieve this ELF's segments and sections
segment regions :  <ELFSegment flags=0x4, relro=0x0, vaddr=0x400000, memsize=0x37a8, filesize=0x37a8, offset=0x0>
segment regions :  <ELFSegment flags=0x5, relro=0x0, vaddr=0x404000, memsize=0x1b04d, filesize=0x1b04d, offset=0x4000>
segment regions :  <ELFSegment flags=0x4, relro=0x0, vaddr=0x420000, memsize=0x7340, filesize=0x7340, offset=0x20000>
segment regions :  <ELFSegment flags=0x4, relro=0x1, vaddr=0x428930, memsize=0x6d0, filesize=0x6d0, offset=0x27930>
segment regions :  <ELFSegment flags=0x6, relro=0x0, vaddr=0x429000, memsize=0x2c88, filesize=0x1830, offset=0x28000>



Section Regions:  <Unnamed | offset 0x0, vaddr 0x400000, size 0x0>
Section Regions:  <.interp | offset 0x318, vaddr 0x400318, size 0x1c>
Section Regions:  <.note.gnu.property | offset 0x338, vaddr 0x400338, size 0x30>
Section Regions:  <.note.gnu.build-id | offset 0x368, vaddr 0x400368, size 0x24>
Section Regions:  <.note.ABI-ta

In [4]:
import os
        
fh = open(filePath, 'rb')
bin_bytearray = bytearray(fh.read())


In [5]:

### SET OF ALL CONDITIONAL JUMPS TAKEN FROM ONLINE SOURCE

JUMP_OPCODES = ['JO','JNO','JS','JNS','JE','JZ','JNE','JNZ','JB','JNAE','JC','JNB','JAE','JNC','JBE','JNA','JA',
'JNBE','JL','JNGE','JGE','JNL','JLE','JNG','JG','JNLE','JP','JPE','JNP','JPO','JCXZ','JECXZ']


In [6]:
# some functions for converting lists

def int_list_to_hex_list(int_list):
    hex_list =[]
    for i in int_list:
        hex_list.append(hex(i))
    return hex_list


def hex_list_to_int_list(hex_list):
    int_list =[]
    for h in hex_list:
        int_list.append(int(i,0))
    return int_list

In [7]:
#took inspiration from capstone github sample code 


from capstone import *
from pprint import pprint

code_section = obj.find_section_containing(obj.entry)
textSectionStart = code_section.offset #int(code_section.offset,0)
textSectionLen =  code_section.filesize#int(code_section.filesize,0)

textSectionEnd = textSectionStart+textSectionLen


address_instruction_info_dict = {}



print('Start: ',hex(code_section.offset) , "end: ", hex(textSectionEnd))

md = Cs(CS_ARCH_X86, CS_MODE_64)


visited_addresses = []
entry_addresses = []
address_and_instructions = []

entry_addresses.append(textSectionStart)
counter = 0



#will loop as long as there are some unexplored entrypoints in the list entry_addresses
while len(entry_addresses)>0:
    
    
    counter+=1
    
    current_entry_address = entry_addresses.pop(0) #take one entry point
    
    if current_entry_address in visited_addresses: #if it was already visited, continue
        continue
    
    
    
    ## I am asking CAPSTONE to disamble as much code as possible in a single go. 
    ##   I am not stopping at a jump or branch. I will dissabmle as much possible and 
    ###    save the targets of jumps and branches for next iteration
    
    CODE = bin_bytearray[current_entry_address: textSectionEnd]
    for i in md.disasm(CODE, current_entry_address ):
        print("0x%x:\t%s\t%s" %(i.address, i.mnemonic, i.op_str))  
        
        address_instruction_info_dict[i.address] = {'address':i.address, 
                                                    'mnemonic':i.mnemonic, 
                                                    'op_str':i.op_str,
                                                    'size': i.size   } 

        address_and_instructions.append([i.address, i.mnemonic, i.op_str])
        
        visited_addresses.append(i.address)

        # IF there is a conditional jump
        if i.mnemonic.upper() in JUMP_OPCODES:
            try:
                if int(i.op_str,0)>=0:
                    if i.op_str not in visited_addresses:
                        
                        entry_addresses.append(int(i.op_str,0))
            except: 
                print('\t\t->->->                               indirect BRUNCH')
                break
        
                # IF there is a  jump
        if i.mnemonic.upper() in ['JMP']:
            print(i.op_str)
            try:
                if int(i.op_str,0)>=0:
                    
                    if int(i.op_str,0)>=textSectionStart and int(i.op_str,0)<=textSectionEnd:
                    
                        if i.op_str not in visited_addresses:
                            entry_addresses.append(int(i.op_str,0))
#                            
                    
                    
            except:
                print('\t\t->->->                                  indirect JMP')
                break
                

Start:  0x4f20 end:  0x1f03e
0x4f20:	mov	byte ptr [rsp + 8], 0
0x4f25:	jmp	0x107fa
0x107fa
0x4f2a:	call	0x4850
0x4f2f:	nop	
0x4f30:	endbr64	
0x4f34:	push	r15
0x4f36:	push	r14
0x4f38:	lea	r14, [rip + 0x1b669]
0x4f3f:	push	r13
0x4f41:	lea	r13, [rip + 0x1b2b4]
0x4f48:	push	r12
0x4f4a:	push	rbp
0x4f4b:	mov	ebp, edi
0x4f4d:	push	rbx
0x4f4e:	mov	rbx, rsi
0x4f51:	sub	rsp, 0x88
0x4f58:	mov	rax, qword ptr fs:[0x28]
0x4f61:	mov	qword ptr [rsp + 0x78], rax
0x4f66:	xor	eax, eax
0x4f68:	mov	dword ptr [rsp + 0x34], 0
0x4f70:	mov	qword ptr [rsp + 0x50], 0
0x4f79:	mov	qword ptr [rsp + 0x58], 0
0x4f82:	call	0x18c50
0x4f87:	lea	rsi, [rip + 0x1d457]
0x4f8e:	mov	edi, 6
0x4f93:	call	0x4d00
0x4f98:	mov	rax, qword ptr [rbx]
0x4f9b:	lea	rdi, [rip + 0x1b5be]
0x4fa2:	mov	qword ptr [rip + 0x2593f], rax
0x4fa9:	call	0x47e0
0x4fae:	lea	rdx, [rip + 0x1c729]
0x4fb5:	test	rax, rax
0x4fb8:	cmove	rax, rdx
0x4fbc:	mov	qword ptr [rip + 0x2592d], rax
0x4fc3:	xor	eax, eax
0x4fc5:	call	0x17660
0x4fca:	xor	eax, eax
0x4fcc:	c

0x127ad:	call	0x49b0
0x127b2:	lea	rdi, [rax + 0x21]
0x127b6:	call	0x1d670
0x127bb:	mov	dword ptr [rsp + 0x18], r15d
0x127c0:	movabs	rdx, 0xa3d70a3d70a3d70b
0x127ca:	mov	r14, rax
0x127cd:	mov	rax, qword ptr [rsp + 8]
0x127d2:	imul	rdx
0x127d5:	mov	rax, qword ptr [rsp + 8]
0x127da:	add	rdx, rax
0x127dd:	sar	rax, 0x3f
0x127e1:	sar	rdx, 6
0x127e5:	sub	rdx, rax
0x127e8:	mov	qword ptr [rsp + 0x30], rdx
0x127ed:	jmp	0x1282b
0x1282b
0x127ef:	nop	
0x127f0:	mov	r8, qword ptr [rsp + 0x10]
0x127f5:	mov	esi, 1
0x127fa:	mov	rdi, r14
0x127fd:	xor	eax, eax
0x127ff:	lea	rcx, [rip + 0xeab8]
0x12806:	mov	rdx, -1
0x1280d:	call	0x4f10
0x12812:	mov	edx, 1
0x12817:	mov	esi, 1
0x1281c:	mov	rdi, r14
0x1281f:	call	0xe480
0x12824:	xor	eax, eax
0x12826:	call	0xa820
0x1282b:	mov	ecx, dword ptr [rip + 0x1927f]
0x12831:	test	ecx, ecx
0x12833:	jne	0x12a30
0x12839:	mov	edi, 1
0x1283e:	call	0x18b70
0x12843:	mov	edi, dword ptr [rsp + 0x18]
0x12847:	mov	edx, 0x8000
0x1284c:	mov	rsi, rbp
0x1284f:	call	0x47a0
0x12854:	xor	

0x12ce7:	mov	rsi, qword ptr [rbp + 0x18]
0x12ceb:	mov	rdi, r15
0x12cee:	call	0x4b30
0x12cf3:	mov	rdx, qword ptr [rbx + 0x38]
0x12cf7:	mov	r8d, eax
0x12cfa:	movsxd	rax, r13d
0x12cfd:	lea	r12, [rax + rax*4]
0x12d01:	shl	r12, 4
0x12d05:	add	rdx, r12
0x12d08:	test	r8d, r8d
0x12d0b:	jne	0x12d39
0x12d0d:	movsxd	rax, r14d
0x12d10:	mov	rdi, qword ptr [rdx]
0x12d13:	mov	qword ptr [rsp + 8], rdx
0x12d18:	lea	rax, [rax + rax*4]
0x12d1c:	shl	rax, 4
0x12d20:	add	rax, qword ptr [rbp + 0x38]
0x12d24:	mov	rsi, qword ptr [rax]
0x12d27:	call	0x4b30
0x12d2c:	mov	rdx, qword ptr [rsp + 8]
0x12d31:	test	eax, eax
0x12d33:	je	0x12e40
0x12d39:	cmp	byte ptr [rdx + 0x48], 1
0x12d3d:	jne	0x12d57
0x12d3f:	movsxd	rax, r14d
0x12d42:	lea	r10, [rax + rax*4]
0x12d46:	mov	rax, qword ptr [rbp + 0x38]
0x12d4a:	shl	r10, 4
0x12d4e:	add	rax, r10
0x12d51:	cmp	byte ptr [rax + 0x48], 1
0x12d55:	je	0x12da0
0x12d57:	mov	ecx, 0x1e
0x12d5c:	xor	edx, edx
0x12d5e:	mov	rsi, r15
0x12d61:	xor	eax, eax
0x12d63:	lea	rdi, [rip + 0xede6]
0x

0x57a1:	cmp	byte ptr [r13 + 0x1b], 0
0x57a6:	mov	rax, qword ptr [r13]
0x57aa:	je	0x67c0
0x57b0:	lea	rdx, [rip + 0x23869]
0x57b7:	sub	rax, rdx
0x57ba:	movabs	rdx, 0xea0ea0ea0ea0ea1
0x57c4:	mov	rcx, rax
0x57c7:	imul	rdx
0x57ca:	mov	rax, rcx
0x57cd:	sar	rax, 0x3f
0x57d1:	sar	rdx, 1
0x57d4:	mov	rbp, rdx
0x57d7:	sub	rbp, rax
0x57da:	not	ebp
0x57dc:	lea	eax, [rbp + 0x57]
0x57df:	cmp	eax, 0x5e
0x57e2:	ja	0x57f5
0x57e4:	lea	rcx, [rip + 0x1aaf1]
0x57eb:	movsxd	rax, dword ptr [rcx + rax*4]
0x57ef:	add	rax, rcx
0x57f2:	jmp	rax
rax
		->->->                                  indirect JMP
0x5057:	mov	rcx, qword ptr [rip + 0x2588a]
0x505e:	mov	rdi, qword ptr [rip + 0x2581b]
0x5065:	lea	rdx, [rip + 0x1b529]
0x506c:	xor	eax, eax
0x506e:	mov	esi, 1
0x5073:	mov	r15d, 1
0x5079:	call	0x4e60
0x507e:	mov	rax, qword ptr [rsp + 0x78]
0x5083:	sub	rax, qword ptr fs:[0x28]
0x508c:	jne	0x7475
0x5092:	add	rsp, 0x88
0x5099:	mov	eax, r15d
0x509c:	pop	rbx
0x509d:	pop	rbp
0x509e:	pop	r12
0x50a0:	pop	r13
0x50a2:	pop	r14


0xd757:	mov	eax, dword ptr [rax + 0xc]
0xd75a:	lea	rbp, [rbx + 3]
0xd75e:	test	eax, eax
0xd760:	je	0xd7f0
0xd766:	mov	edx, dword ptr [rip + 0x1caa4]
0xd76c:	mov	esi, dword ptr [rip + 0x1ca9a]
0xd772:	mov	edi, dword ptr [rip + 0x1ca9c]
0xd778:	call	0xa570
0xd77d:	mov	rcx, qword ptr [rip + 0x1dc84]
0xd784:	cmp	r12, rbp
0xd787:	jb	0xd810
0xd78d:	mov	rsi, qword ptr [rcx + 0x18]
0xd791:	mov	rdx, qword ptr [rcx + 0x40]
0xd795:	xor	ebx, ebx
0xd797:	mov	rdi, qword ptr [rcx + 0x28]
0xd79b:	mov	rax, rdi
0xd79e:	sub	rax, rdx
0xd7a1:	mov	edx, 1
0xd7a6:	mov	r8, rax
0xd7a9:	shr	r8, 2
0xd7ad:	cmp	rax, 3
0xd7b1:	cmova	edx, r8d
0xd7b5:	xor	eax, eax
0xd7b7:	cmp	rdi, rsi
0xd7ba:	ja	0xd7d3
0xd7bc:	mov	rax, rsi
0xd7bf:	sub	rax, rdi
0xd7c2:	movsxd	rdi, edx
0xd7c5:	lea	r8d, [rdx + rax]
0xd7c9:	xor	edx, edx
0xd7cb:	div	rdi
0xd7ce:	mov	eax, r8d
0xd7d1:	sub	eax, edx
0xd7d3:	mov	edx, esi
0xd7d5:	mov	rdi, qword ptr [rcx]
0xd7d8:	xor	esi, esi
0xd7da:	sub	edx, eax
0xd7dc:	call	0xc680
0xd7e1:	cmp	r12, rbp
0xd7e4:	jb

...

0x75ad:	add	rsp, 0x10
0x75b1:	mov	eax, r12d
0x75b4:	pop	r12
0x75b6:	ret	
0x75b7:	nop	word ptr [rax + rax]
0x75c0:	xor	eax, eax
0x75c2:	mov	r12d, 1
0x75c8:	call	0xcb30
0x75cd:	jmp	0x75ad
0x75ad
0x75cf:	nop	
0x75d0:	xor	eax, eax
0x75d2:	mov	r12d, 1
0x75d8:	call	0xcb60
0x75dd:	jmp	0x75ad
0x75ad
0x75df:	nop	
0x75e0:	xor	eax, eax
0x75e2:	mov	r12d, 1
0x75e8:	call	0xcc30
0x75ed:	jmp	0x75ad
0x75ad
0x75ef:	nop	
0x75f0:	xor	eax, eax
0x75f2:	mov	r12d, 1
0x75f8:	call	0xccf0
0x75fd:	jmp	0x75ad
0x75ad
0x75ff:	nop	
0x7600:	xor	eax, eax
0x7602:	mov	r12d, 1
0x7608:	call	0xcd10
0x760d:	jmp	0x75ad
0x75ad
0x760f:	nop	
0x7610:	and	r12d, 1
0x7614:	jne	0x7820
0x761a:	mov	r12d, 1
0x7620:	add	rsp, 0x10
0x7624:	mov	eax, r12d
0x7627:	pop	r12
0x7629:	ret	
0x762a:	nop	word ptr [rax + rax]
0x7630:	and	r12d, 1
0x7634:	je	0x761a
0x7636:	xor	eax, eax
0x7638:	call	0xce70
0x763d:	jmp	0x75ad
0x75ad
0x7642:	nop	word ptr [rax + rax]
0x7648:	and	r12d, 1
0x764c:	je	0x761a
0x764e:	xor	eax, eax
0x7650:	call	0xd380
0x7655:	jmp	

0x83cb:	test	r13, r13
0x83ce:	jne	0x8202
0x83d4:	jmp	0x8229
0x8229
0x83d9:	call	0x49d0
0x83de:	nop	
0x83e0:	endbr64	
0x83e4:	push	r15
0x83e6:	push	r14
0x83e8:	mov	r14, rdi
0x83eb:	push	r13
0x83ed:	mov	r13, rsi
0x83f0:	push	r12
0x83f2:	mov	r12, rdx
0x83f5:	push	rbp
0x83f6:	mov	rbp, rcx
0x83f9:	push	rbx
0x83fa:	sub	rsp, 0x38
0x83fe:	mov	rax, qword ptr fs:[0x28]
0x8407:	mov	qword ptr [rsp + 0x28], rax
0x840c:	xor	eax, eax
0x840e:	call	0xcff0
0x8413:	test	r14, r14
0x8416:	je	0x8420
0x8418:	mov	rdi, r14
0x841b:	call	0xd540
0x8420:	test	r12, r12
0x8423:	je	0x8450
0x8425:	mov	rdi, r12
0x8428:	call	0xd610
0x842d:	test	rbp, rbp
0x8430:	je	0x8450
0x8432:	mov	rsi, r12
0x8435:	mov	rdi, rbp
0x8438:	xor	eax, eax
0x843a:	mov	r14d, 1
0x8440:	call	0x7e00
0x8445:	jmp	0x8453
0x8453
0x8447:	nop	word ptr [rax + rax]
0x8450:	xor	r14d, r14d
0x8453:	xor	eax, eax
0x8455:	lea	r12, [rsp + 0x1c]
0x845a:	lea	rbx, [rip + 0x17c03]
0x8461:	call	0xd870
0x8466:	xor	eax, eax
0x8468:	call	0xd740
0x846d:	xor	eax, eax
0x84

0x1e750:	cmp	dl, 0x7c
0x1e753:	je	0x1e20a
0x1e759:	jmp	0x1e240
0x1e240
0x1e75e:	nop	
0x1e760:	lea	rax, [r12 + 2]
0x1e765:	lea	r15, [r12 + 1]
0x1e76a:	mov	ebp, 0x3f
0x1e76f:	cmp	rax, r13
0x1e772:	jae	0x1e1a4
0x1e778:	cmp	byte ptr [r11 + r12 + 1], 0x3f
0x1e77e:	jne	0x1e1a4
0x1e784:	movzx	ebp, byte ptr [r11 + r12 + 2]
0x1e78a:	cmp	bpl, 0x3e
0x1e78e:	ja	0x1e7a4
0x1e790:	movabs	rax, 0x7000a38200000000
0x1e79a:	bt	rax, rbp
0x1e79e:	jb	0x1e8f9
0x1e7a4:	mov	ebp, 0x3f
0x1e7a9:	jmp	0x1e1a4
0x1e1a4
0x1e7ae:	test	r12, r12
0x1e7b1:	jne	0x1e7be
0x1e7b3:	cmp	dword ptr [rsp + 0x10], 1
0x1e7b8:	je	0x1e380
0x1e7be:	mov	rsi, qword ptr [rsp + 0x20]
0x1e7c3:	mov	rax, rbx
0x1e7c6:	test	rsi, rsi
0x1e7c9:	je	0x1e7f4
0x1e7cb:	movzx	edx, byte ptr [rsi]
0x1e7ce:	test	dl, dl
0x1e7d0:	je	0x1e7f4
0x1e7d2:	sub	rsi, rbx
0x1e7d5:	mov	rcx, rsi
0x1e7d8:	mov	rsi, qword ptr [rsp + 8]
0x1e7dd:	nop	dword ptr [rax]
0x1e7e0:	cmp	r10, rax
0x1e7e3:	jbe	0x1e7e8
0x1e7e5:	mov	byte ptr [rsi + rax], dl
0x1e7e8:	add	rax, 1
0x1e7ec:	m

0x1e7c3:	mov	rax, rbx
0x1e7c6:	test	rsi, rsi
0x1e7c9:	je	0x1e7f4
0x1e7cb:	movzx	edx, byte ptr [rsi]
0x1e7ce:	test	dl, dl
0x1e7d0:	je	0x1e7f4
0x1e7d2:	sub	rsi, rbx
0x1e7d5:	mov	rcx, rsi
0x1e7d8:	mov	rsi, qword ptr [rsp + 8]
0x1e7dd:	nop	dword ptr [rax]
0x1e7e0:	cmp	r10, rax
0x1e7e3:	jbe	0x1e7e8
0x1e7e5:	mov	byte ptr [rsi + rax], dl
0x1e7e8:	add	rax, 1
0x1e7ec:	movzx	edx, byte ptr [rcx + rax]
0x1e7f0:	test	dl, dl
0x1e7f2:	jne	0x1e7e0
0x1e7f4:	cmp	rax, r10
0x1e7f7:	jae	0x1e802
0x1e7f9:	mov	rsi, qword ptr [rsp + 8]
0x1e7fe:	mov	byte ptr [rsi + rax], 0
0x1e802:	mov	rdx, qword ptr [rsp + 0x78]
0x1e807:	sub	rdx, qword ptr fs:[0x28]
0x1e810:	jne	0x1e9ca
0x1e816:	add	rsp, 0x88
0x1e81d:	pop	rbx
0x1e81e:	pop	rbp
0x1e81f:	pop	r12
0x1e821:	pop	r13
0x1e823:	pop	r14
0x1e825:	pop	r15
0x1e827:	ret	
0x1e828:	mov	eax, r8d
0x1e82b:	xor	ecx, ecx
0x1e82d:	jmp	0x1e299
0x1e299
0x1e832:	mov	eax, dword ptr [rsp + 0x10]
0x1e836:	jbe	0x1e88a
0x1e838:	sub	eax, 5
0x1e83b:	cmp	eax, 1
0x1e83e:	ja	0x1e8c8
0x1e844:	cmp

0x1e4e0:	cmp	dl, 0x7d
0x1e4e3:	je	0x1e72c
0x1e4e9:	jle	0x1e1f8
0x1e4ef:	cmp	dl, 0x7e
0x1e4f2:	je	0x1e365
0x1e4f8:	nop	dword ptr [rax + rax]
0x1e500:	lea	r14, [r12 + 1]
0x1e505:	cmp	qword ptr [rsp + 0x28], 1
0x1e50b:	mov	byte ptr [rsp + 0x30], dl
0x1e50f:	mov	r15, r14
0x1e512:	je	0x1e250
0x1e518:	mov	qword ptr [rsp + 0x70], 0
0x1e521:	lea	rcx, [rsp + 0x70]
0x1e526:	cmp	r13, -1
0x1e52a:	jne	0x1e574
0x1e52c:	mov	rdi, r11
0x1e52f:	mov	qword ptr [rsp + 0x58], r10
0x1e534:	mov	byte ptr [rsp + 0x50], r8b
0x1e539:	mov	qword ptr [rsp + 0x48], r9
0x1e53e:	mov	qword ptr [rsp + 0x40], rsi
0x1e543:	mov	qword ptr [rsp + 0x38], rcx
0x1e548:	mov	qword ptr [rsp + 0x30], r11
0x1e54d:	call	0x49b0
0x1e552:	mov	r10, qword ptr [rsp + 0x58]
0x1e557:	movzx	r8d, byte ptr [rsp + 0x50]
0x1e55d:	mov	r9, qword ptr [rsp + 0x48]
0x1e562:	mov	rsi, qword ptr [rsp + 0x40]
0x1e567:	mov	r13, rax
0x1e56a:	mov	rcx, qword ptr [rsp + 0x38]
0x1e56f:	mov	r11, qword ptr [rsp + 0x30]
0x1e574:	mov	rdx, r13
0x1e577:	lea	rdi, [rsp 

In [8]:
# sorting the instruction according to address, for easier printing


address_keys = list(address_instruction_info_dict.keys())
address_keys.sort()
address_instruction_info_dict = {i: address_instruction_info_dict[i] for i in address_keys}


In [9]:
# display and save into file



current_address = code_section.offset


is_new_block = False

with open('instructions.s', 'w') as out_file:
    while current_address<textSectionEnd:
        
        if current_address in address_instruction_info_dict:

            if is_new_block == True:
                print('\n\n')
                print("0x%x:\t ----------" %(current_address-2))
                print("0x%x:\t ----------" %(current_address-1))
                
                out_file.write("0x%x:\t ----------" %(current_address-1)+ '\n')
                
                
            is_new_block = False


            info = address_instruction_info_dict[current_address]
            print("0x%x:\t%s\t%s" %(info['address'], 
                                info['mnemonic'], info['op_str'])) 
            out_file.write("0x%x:\t%s\t%s" %(info['address'], 
                                info['mnemonic'], info['op_str'])+ '\n')
            
            current_address+= info['size']

        else:

            if is_new_block == False:
                print("0x%x:\t ----------" %(current_address))
                out_file.write("0x%x:\t ----------" %(current_address)+ '\n')
                
            current_address+=1
            is_new_block = True



0x4f20:	mov	byte ptr [rsp + 8], 0
0x4f25:	jmp	0x107fa
0x4f2a:	call	0x4850
0x4f2f:	nop	
0x4f30:	endbr64	
0x4f34:	push	r15
0x4f36:	push	r14
0x4f38:	lea	r14, [rip + 0x1b669]
0x4f3f:	push	r13
0x4f41:	lea	r13, [rip + 0x1b2b4]
0x4f48:	push	r12
0x4f4a:	push	rbp
0x4f4b:	mov	ebp, edi
0x4f4d:	push	rbx
0x4f4e:	mov	rbx, rsi
0x4f51:	sub	rsp, 0x88
0x4f58:	mov	rax, qword ptr fs:[0x28]
0x4f61:	mov	qword ptr [rsp + 0x78], rax
0x4f66:	xor	eax, eax
0x4f68:	mov	dword ptr [rsp + 0x34], 0
0x4f70:	mov	qword ptr [rsp + 0x50], 0
0x4f79:	mov	qword ptr [rsp + 0x58], 0
0x4f82:	call	0x18c50
0x4f87:	lea	rsi, [rip + 0x1d457]
0x4f8e:	mov	edi, 6
0x4f93:	call	0x4d00
0x4f98:	mov	rax, qword ptr [rbx]
0x4f9b:	lea	rdi, [rip + 0x1b5be]
0x4fa2:	mov	qword ptr [rip + 0x2593f], rax
0x4fa9:	call	0x47e0
0x4fae:	lea	rdx, [rip + 0x1c729]
0x4fb5:	test	rax, rax
0x4fb8:	cmove	rax, rdx
0x4fbc:	mov	qword ptr [rip + 0x2592d], rax
0x4fc3:	xor	eax, eax
0x4fc5:	call	0x17660
0x4fca:	xor	eax, eax
0x4fcc:	call	0x18420
0x4fd1:	xor	eax, eax
0x4f




0x84ee:	 ----------
0x84ef:	 ----------
0x84f0:	mov	esi, 3
0x84f5:	mov	edi, r15d
0x84f8:	call	0x7570
0x84fd:	test	eax, eax
0x84ff:	je	0x8670
0x8505:	mov	eax, dword ptr [rsp + 0x1c]
0x8509:	lea	edx, [rax - 1]
0x850c:	mov	dword ptr [rsp + 0x1c], edx
0x8510:	test	eax, eax
0x8512:	jne	0x84f0
0x8514:	call	0xd870
0x8519:	xor	eax, eax
0x851b:	call	0xdea0
0x8520:	xor	eax, eax
0x8522:	call	0xd740
0x8527:	xor	eax, eax
0x8529:	call	0xa820
0x852e:	mov	rdi, r12
0x8531:	call	0xb180
0x8536:	test	rax, rax
0x8539:	jne	0x848e
0x853f:	xor	eax, eax
0x8541:	call	0xa5a0
0x8546:	xor	eax, eax
0x8548:	call	0xdea0
0x854d:	xor	eax, eax
0x854f:	call	0xd740
0x8554:	jmp	0x847d
0x8559:	nop	dword ptr [rax]
0x8560:	mov	rdi, r13
0x8563:	call	0xdb10
0x8568:	test	rbp, rbp
0x856b:	je	0x857b
0x856d:	mov	rsi, qword ptr [r13]
0x8571:	mov	rdi, rbp
0x8574:	xor	eax, eax
0x8576:	call	0x7e00
0x857b:	mov	rax, qword ptr [r13]
0x857f:	mov	rdx, qword ptr [rsp + 0x28]
0x8584:	sub	rdx, qword ptr fs:[0x28]
0x858d:	jne	0x86b3
0x8593:	

0xaa04:	idiv	dword ptr [rip + 0x1ff8e]
0xaa0a:	mov	r14d, edx
0xaa0d:	cmp	edx, r13d
0xaa10:	je	0xa8bb
0xaa16:	nop	word ptr cs:[rax + rax]
0xaa20:	mov	esi, r14d
0xaa23:	mov	edi, eax
0xaa25:	mov	dword ptr [rsp + 4], eax
0xaa29:	mov	r13d, r14d
0xaa2c:	call	0xa7a0
0xaa31:	jmp	0xa8c5
0xaa36:	nop	word ptr cs:[rax + rax]
0xaa40:	movzx	edx, byte ptr [rip + 0x20909]
0xaa47:	and	edx, 7
0xaa4a:	cmp	eax, edx
0xaa4c:	je	0xa92e
0xaa52:	cmp	dword ptr [rip + 0x1f207], 1
0xaa59:	jne	0xa903
0xaa5f:	mov	eax, dword ptr [rip + 0x164b4]
0xaa65:	mov	edx, dword ptr [rip + 0x2049d]
0xaa6b:	mov	dword ptr [rsp + 0x10], eax
0xaa6f:	movzx	eax, byte ptr [rip + 0x164a7]
0xaa76:	mov	byte ptr [rsp + 0x14], al
0xaa7a:	lea	eax, [r14 + 0x30]
0xaa7e:	mov	byte ptr [rsp + 0x13], al
0xaa82:	cmp	edx, 0x3fa
0xaa88:	jg	0xac18
0xaa8e:	movsxd	rax, edx
0xaa91:	add	edx, 5
0xaa94:	add	rax, r12
0xaa97:	mov	ecx, dword ptr [rsp + 0x10]
0xaa9b:	mov	dword ptr [rip + 0x20467], edx
0xaaa1:	mov	dword ptr [rax], ecx
0xaaa3:	movzx	ecx, byte pt

0xe3b5:	mov	qword ptr [r12], rax
0xe3b9:	mov	eax, edx
0xe3bb:	mov	rcx, qword ptr [r10 + rax - 8]
0xe3c0:	mov	qword ptr [r12 + rax - 8], rcx
0xe3c5:	sub	r12, rsi
0xe3c8:	sub	r10, r12
0xe3cb:	add	r12d, edx
0xe3ce:	and	r12d, 0xfffffff8
0xe3d2:	cmp	r12d, 8
0xe3d6:	jb	0xe2d7
0xe3dc:	mov	r11d, dword ptr [rbp - 0x74]
0xe3e0:	and	r12d, 0xfffffff8
0xe3e4:	xor	eax, eax
0xe3e6:	mov	ecx, eax
0xe3e8:	add	eax, 8
0xe3eb:	mov	rdi, qword ptr [r10 + rcx]
0xe3ef:	mov	qword ptr [rsi + rcx], rdi
0xe3f3:	cmp	eax, r12d
0xe3f6:	jb	0xe3e6
0xe3f8:	mov	dword ptr [rbp - 0x74], r11d
0xe3fc:	jmp	0xe2d7
0xe401:	nop	dword ptr [rax]
0xe408:	movzx	eax, byte ptr [rcx]
0xe40b:	mov	byte ptr [r12], al
0xe40f:	test	dl, 2
0xe412:	je	0xe1a7
0xe418:	mov	eax, edx
0xe41a:	movzx	ecx, word ptr [rcx + rax - 2]
0xe41f:	mov	word ptr [r12 + rax - 2], cx
0xe425:	jmp	0xe1a7
0xe42a:	nop	word ptr [rax + rax]
0xe430:	mov	rax, r13
0xe433:	jmp	0xdfc7
0xe438:	mov	eax, dword ptr [rcx]
0xe43a:	mov	dword ptr [r12], eax
0xe43e:	mov	eax, edx
0xe44

0x11e31:	call	0x18f40
0x11e36:	cmp	eax, -1
0x11e39:	je	0x121c8
0x11e3f:	mov	rax, qword ptr [rsp + 0xa0]
0x11e47:	cmp	qword ptr [rsp + 0x10], rax
0x11e4c:	jne	0x11e5a
0x11e4e:	mov	eax, dword ptr [r14 + 0x10]
0x11e52:	test	eax, eax
0x11e54:	je	0x12188
0x11e5a:	mov	r9d, dword ptr [rsp + 0xc0]
0x11e62:	mov	rdx, r12
0x11e65:	mov	rsi, rbp
0x11e68:	xor	eax, eax
0x11e6a:	mov	r8d, dword ptr [rsp + 0xbc]
0x11e72:	mov	ecx, dword ptr [rsp + 0xb8]
0x11e79:	mov	rdi, r14
0x11e7c:	call	0x11330
0x11e81:	mov	r13d, eax
0x11e84:	cmp	eax, 3
0x11e87:	je	0x11ea1
0x11e89:	jg	0x120d0
0x11e8f:	cmp	eax, 1
0x11e92:	je	0x121a8
0x11e98:	cmp	eax, 2
0x11e9b:	jne	0x12210
0x11ea1:	mov	rax, qword ptr [rsp + 0x138]
0x11ea9:	sub	rax, qword ptr fs:[0x28]
0x11eb2:	jne	0x122c1
0x11eb8:	add	rsp, 0x148
0x11ebf:	mov	eax, r13d
0x11ec2:	pop	rbx
0x11ec3:	pop	rbp
0x11ec4:	pop	r12
0x11ec6:	pop	r13
0x11ec8:	pop	r14
0x11eca:	pop	r15
0x11ecc:	ret	
0x11ecd:	nop	dword ptr [rax]
0x11ed0:	mov	eax, dword ptr [rsp + 0x28]
0x11ed4:	and	eax, 0

0x14810:	lea	rax, [rcx + 0x49]
0x14814:	lea	rdx, [rcx + rdx + 0x99]
0x1481c:	nop	dword ptr [rax]
0x14820:	cmp	byte ptr [rax], 0
0x14823:	jne	0x14832
0x14825:	cmp	byte ptr [rax - 1], 0
0x14829:	je	0x14832
0x1482b:	mov	byte ptr [rax], 1
0x1482e:	add	dword ptr [rbp + 0x70], 1
0x14832:	add	rax, 0x50
0x14836:	cmp	rax, rdx
0x14839:	jne	0x14820
0x1483b:	jmp	0x14132
0x14840:	test	al, al
0x14842:	jne	0x140f0
0x14848:	mov	byte ptr [r12 + 0x49], 1
0x1484e:	add	dword ptr [rbp + 0x70], 1
0x14852:	jmp	0x140f0
0x14857:	lea	rdi, [rip + 0xcb3a]
0x1485e:	call	0x8b00
0x14863:	jmp	0x13f50
0x14868:	nop	dword ptr [rax + rax]
0x14870:	test	r13d, r13d
0x14873:	je	0x14931
0x14879:	test	dl, dl
0x1487b:	je	0x13f50
0x14881:	mov	rdi, rbp
0x14884:	xor	eax, eax
0x14886:	call	0x10d70
0x1488b:	movzx	edx, byte ptr [rbp + 0x6d]
0x1488f:	test	dl, dl
0x14891:	jne	0x14150
0x14897:	jmp	0x13f50
0x1489c:	nop	dword ptr [rax]
0x148a0:	test	r13d, r13d
0x148a3:	je	0x14956
0x148a9:	test	dil, dil
0x148ac:	je	0x13f50
0x148b2:	mov	rd

0x17d4d:	xor	esi, esi
0x17d4f:	call	0x4ba0
0x17d54:	mov	rdx, qword ptr [rsp + 8]
0x17d59:	sub	rdx, qword ptr fs:[0x28]
0x17d62:	jne	0x17d6a
0x17d64:	add	rsp, 0x10
0x17d68:	pop	rbx
0x17d69:	ret	
0x17d6a:	call	0x49d0
0x17d6f:	nop	
0x17d70:	endbr64	
0x17d74:	push	r15
0x17d76:	push	r14
0x17d78:	mov	r14, rdi
0x17d7b:	push	r13
0x17d7d:	mov	r13d, ecx
0x17d80:	mov	ecx, 1
0x17d85:	push	r12
0x17d87:	mov	r12d, r13d
0x17d8a:	push	rbp
0x17d8b:	mov	ebp, edx
0x17d8d:	mov	edx, 1
0x17d92:	push	rbx
0x17d93:	mov	rbx, rsi
0x17d96:	sub	rsp, 0x18
0x17d9a:	mov	rax, qword ptr fs:[0x28]
0x17da3:	mov	qword ptr [rsp + 8], rax
0x17da8:	xor	eax, eax
0x17daa:	mov	rsi, rsp
0x17dad:	call	0x17320
0x17db2:	mov	r15, qword ptr [rsp]
0x17db6:	test	r15, r15
0x17db9:	je	0x17de4
0x17dbb:	test	ebp, ebp
0x17dbd:	jle	0x17e3c
0x17dbf:	xor	r12d, r12d
0x17dc2:	jmp	0x17dd5
0x17dc4:	nop	dword ptr [rax]
0x17dc8:	add	r12d, 1
0x17dcc:	add	rbx, 8
0x17dd0:	cmp	ebp, r12d
0x17dd3:	je	0x17e10
0x17dd5:	mov	rsi, qword ptr [rbx]
0x17dd8:	mov	r

0x1b0c0:	cmp	r14b, 0x20
0x1b0c4:	je	0x1b0a8
0x1b0c6:	cmp	r14b, 9
0x1b0ca:	je	0x1b0a8
0x1b0cc:	cmp	byte ptr [rip + 0x10a0d], r14b
0x1b0d3:	je	0x1b315
0x1b0d9:	movsx	r15d, r14b
0x1b0dd:	lea	rdi, [rip + 0x7379]
0x1b0e4:	mov	esi, r15d
0x1b0e7:	call	0x4a00
0x1b0ec:	test	rax, rax
0x1b0ef:	je	0x1b190
0x1b0f5:	add	ebx, 1
0x1b0f8:	mov	r14d, 1
0x1b0fe:	mov	r9d, 2
0x1b104:	movsxd	rbp, ebx
0x1b107:	lea	rcx, [r12 + rbp]
0x1b10b:	mov	eax, dword ptr [rsp + 8]
0x1b10f:	add	eax, 2
0x1b112:	cmp	eax, dword ptr [rsp + 0xc]
0x1b116:	jge	0x1b2a0
0x1b11c:	movsxd	r8, dword ptr [rsp + 8]
0x1b121:	mov	rdx, qword ptr [rsp]
0x1b125:	mov	rdi, r9
0x1b128:	mov	qword ptr [rsp + 0x18], rcx
0x1b12d:	shl	r8, 3
0x1b131:	lea	r15, [rdx + r8]
0x1b135:	mov	qword ptr [rsp + 0x10], r8
0x1b13a:	call	0x1d670
0x1b13f:	mov	rdx, r14
0x1b142:	mov	rsi, r13
0x1b145:	mov	qword ptr [r15], rax
0x1b148:	mov	rdi, rax
0x1b14b:	call	0x4880
0x1b150:	mov	rax, qword ptr [r15]
0x1b153:	mov	r8, qword ptr [rsp + 0x10]
0x1b158:	mov	rcx, qword ptr [

0x1e088:	mov	r11, qword ptr [rsp + 0x20]
0x1e08d:	mov	r10, qword ptr [rsp + 0x30]
0x1e092:	mov	qword ptr [rsp + 0x28], rax
0x1e097:	jne	0x1e832
0x1e09d:	mov	qword ptr [rsp + 0x20], 0
0x1e0a6:	mov	r8d, 1
0x1e0ac:	xor	r9d, r9d
0x1e0af:	nop	
0x1e0b0:	mov	rbx, r9
0x1e0b3:	xor	r12d, r12d
0x1e0b6:	nop	word ptr cs:[rax + rax]
0x1e0c0:	cmp	r13, r12
0x1e0c3:	setne	al
0x1e0c6:	cmp	r13, -1
0x1e0ca:	jne	0x1e0d4
0x1e0cc:	cmp	byte ptr [r11 + r12], 0
0x1e0d1:	setne	al
0x1e0d4:	test	al, al
0x1e0d6:	je	0x1e7ae
0x1e0dc:	lea	rsi, [r11 + r12]
0x1e0e0:	movzx	edx, byte ptr [rsi]
0x1e0e3:	test	r9, r9
0x1e0e6:	je	0x1e4b0
0x1e0ec:	test	r8b, r8b
0x1e0ef:	je	0x1e4b0
0x1e0f5:	lea	r14, [r12 + 1]
0x1e0fa:	mov	r15, r14
0x1e0fd:	cmp	r14, r13
0x1e100:	ja	0x1e120
0x1e102:	mov	rax, qword ptr [rsp + 0x20]
0x1e107:	cmp	byte ptr [rax], dl
0x1e109:	jne	0x1e120
0x1e10b:	cmp	rbx, r10
0x1e10e:	jae	0x1e11c
0x1e110:	mov	rax, qword ptr [rsp + 8]
0x1e115:	mov	byte ptr [rax + rbx], 0x5c
0x1e119:	movzx	edx, byte ptr [rsi]
0x1e11c:	a

In [10]:
# loading again as angr project for comparing the output dissembled code


import os
import angr



base_addr = 0x100000
p = angr.Project(filePath, auto_load_libs=False ,load_options = {'main_opts':{'base_addr': base_addr}})
cfg = p.analyses.CFGFast()
cfg.normalize()
    
    
    

ERROR    | 2023-02-26 17:40:05,090 | angr.analyses.propagator.engine_vex.SimEnginePropagatorVEX | Unsupported Binop Iop_MullS64.
ERROR    | 2023-02-26 17:40:05,116 | angr.analyses.propagator.engine_vex.SimEnginePropagatorVEX | Unsupported Binop Iop_MullS64.
ERROR    | 2023-02-26 17:40:06,783 | angr.analyses.propagator.engine_vex.SimEnginePropagatorVEX | Unsupported Binop Iop_F64toI32S.
ERROR    | 2023-02-26 17:40:06,788 | angr.analyses.propagator.engine_vex.SimEnginePropagatorVEX | Unsupported Binop Iop_F64toI32S.
ERROR    | 2023-02-26 17:40:06,981 | angr.analyses.propagator.engine_vex.SimEnginePropagatorVEX | Unsupported Binop Iop_MullS64.
ERROR    | 2023-02-26 17:40:07,048 | angr.analyses.propagator.engine_vex.SimEnginePropagatorVEX | Unsupported Binop Iop_MullS64.
ERROR    | 2023-02-26 17:40:07,653 | angr.analyses.propagator.engine_vex.SimEnginePropagatorVEX | Unsupported Binop Iop_64HLto128.


In [11]:
# using angrs basic graph travarsal method
#https://stackoverflow.com/questions/74457578/clean-angr-disassemble-output


with open('angr.s', 'w') as angr_file:
    
    for func_node in cfg.functions.values():
            for block in func_node.blocks:
                c = block.capstone

                for i in c.insns:
    #                 print(i)
                    print("0x%x:\t%s\t%s" %(i.address, 
                                    i.mnemonic, i.op_str))
                    angr_file.write("0x%x:\t%s\t%s" %(i.address, 
                                    i.mnemonic, i.op_str)+'\n')


0x104000:	endbr64	
0x104004:	sub	rsp, 8
0x104008:	mov	rax, qword ptr [rip + 0x24fd9]
0x10400f:	test	rax, rax
0x104012:	je	0x104016
0x104016:	add	rsp, 8
0x10401a:	ret	
0x104014:	call	rax
0x104020:	push	qword ptr [rip + 0x24be2]
0x104026:	bnd jmp	qword ptr [rip + 0x24be3]
0x10402d:	nop	dword ptr [rax]
0x104030:	endbr64	
0x104034:	push	0
0x104039:	bnd jmp	0x104020
0x10403f:	nop	
0x104040:	endbr64	
0x104044:	push	1
0x104049:	bnd jmp	0x104020
0x10404f:	nop	
0x104050:	endbr64	
0x104054:	push	2
0x104059:	bnd jmp	0x104020
0x10405f:	nop	
0x104060:	endbr64	
0x104064:	push	3
0x104069:	bnd jmp	0x104020
0x10406f:	nop	
0x104070:	endbr64	
0x104074:	push	4
0x104079:	bnd jmp	0x104020
0x10407f:	nop	
0x104080:	endbr64	
0x104084:	push	5
0x104089:	bnd jmp	0x104020
0x10408f:	nop	
0x104090:	endbr64	
0x104094:	push	6
0x104099:	bnd jmp	0x104020
0x10409f:	nop	
0x1040a0:	endbr64	
0x1040a4:	push	7
0x1040a9:	bnd jmp	0x104020
0x1040af:	nop	
0x1040b0:	endbr64	
0x1040b4:	push	8
0x1040b9:	bnd jmp	0x104020
0x1040bf:	no

0x105fe6:	mov	r8, r14
0x105fe9:	mov	rcx, rbp
0x105fec:	test	eax, eax
0x105fee:	jne	0x105ff3
0x105ff0:	mov	rcx, r12
0x105ff3:	or	rdx, 0xffffffffffffffff
0x105ff7:	mov	esi, 1
0x105ffc:	mov	rdi, r13
0x105fff:	xor	eax, eax
0x106001:	call	0x104f10
0x105ff3:	or	rdx, 0xffffffffffffffff
0x105ff7:	mov	esi, 1
0x105ffc:	mov	rdi, r13
0x105fff:	xor	eax, eax
0x106001:	call	0x104f10
0x106006:	mov	rdi, r13
0x106009:	call	0x1049b0
0x10600e:	mov	rdi, r13
0x106011:	mov	rsi, rax
0x106014:	call	0x1184d0
0x106019:	mov	rdi, r13
0x10601c:	call	0x10d610
0x106021:	mov	rdi, r13
0x106024:	call	0x118d10
0x106059:	mov	rdi, r14
0x10605c:	call	0x10c7e0
0x106061:	mov	rdi, r15
0x106064:	call	0x10db10
0x106069:	mov	rbp, qword ptr [rsp + 0x50]
0x10606e:	mov	rdi, rbp
0x106071:	call	0x1049b0
0x106076:	sub	eax, 1
0x106079:	movsxd	rdx, eax
0x10607c:	jmp	0x106097
0x106097:	test	eax, eax
0x106099:	jns	0x10607e
0x10609b:	movzx	eax, byte ptr [rbp]
0x10609f:	cmp	al, 0x2b
0x1060a1:	je	0x1071c7
0x10607e:	lea	rcx, [rbp + rdx]
0x1060

0x10862b:	mov	rsi, qword ptr [rsp]
0x10862f:	mov	rdi, rbp
0x108632:	mov	edx, r14d
0x108635:	call	0x119200
0x108536:	test	rax, rax
0x108539:	jne	0x10848e
0x1085ec:	mov	rdi, qword ptr [rsp + 8]
0x1085f1:	call	0x10d610
0x108693:	jmp	0x108519
0x108652:	xor	eax, eax
0x108654:	call	0x10d740
0x10863a:	mov	rdi, rax
0x10863d:	test	rax, rax
0x108640:	cmovne	rdi, qword ptr [rsp + 0x20]
0x108646:	call	0x10d610
0x1085f6:	xor	eax, eax
0x1085f8:	call	0x10d870
0x108659:	jmp	0x108519
0x1085fd:	xor	eax, eax
0x1085ff:	call	0x10d740
0x108604:	jmp	0x108519
0x108447:	nop	word ptr [rax + rax]
0x1084ea:	nop	word ptr [rax + rax]
0x108559:	nop	dword ptr [rax]
0x1085a2:	nop	word ptr [rax + rax]
0x108609:	nop	dword ptr [rax]
0x10865e:	nop	
0x10866e:	nop	
0x10867a:	nop	word ptr [rax + rax]
0x108698:	nop	dword ptr [rax + rax]
0x1086b8:	nop	dword ptr [rax + rax]
0x1086c0:	endbr64	
0x1086c4:	push	r15
0x1086c6:	push	r14
0x1086c8:	push	r13
0x1086ca:	push	r12
0x1086cc:	push	rbp
0x1086cd:	push	rbx
0x1086ce:	sub	rsp, 0x18

0x10a800:	xor	eax, eax
0x10a802:	call	0x10a6c0
0x10a7b6:	mov	eax, ebp
0x10a7b8:	mov	esi, dword ptr [rip + 0x201da]
0x10a7be:	mov	edx, dword ptr [rip + 0x201d8]
0x10a7c4:	or	eax, r12d
0x10a7c7:	mov	rdi, qword ptr [rip + 0x1f63a]
0x10a7ce:	js	0x10a7d4
0x10a807:	jmp	0x10a7b6
0x10a7d4:	sub	edx, 1
0x10a7d7:	sub	esi, 1
0x10a7da:	call	0x104960
0x10a7d0:	cmp	ebp, esi
0x10a7d2:	jl	0x10a810
0x10a7df:	add	rsp, 8
0x10a7e3:	mov	esi, 1
0x10a7e8:	lea	rdx, [rip - 0xd7f]
0x10a7ef:	pop	rbp
0x10a7f0:	mov	rdi, rax
0x10a7f3:	pop	r12
0x10a7f5:	jmp	0x104820
0x10a810:	cmp	r12d, edx
0x10a813:	jge	0x10a7d4
0x10a815:	mov	edx, r12d
0x10a818:	mov	esi, ebp
0x10a81a:	jmp	0x10a7da
0x10a7da:	call	0x104960
0x10a7fa:	nop	word ptr [rax + rax]
0x10a809:	nop	dword ptr [rax]
0x10a81c:	nop	dword ptr [rax]
0x10a820:	endbr64	
0x10a824:	push	r15
0x10a826:	push	r14
0x10a828:	push	r13
0x10a82a:	push	r12
0x10a82c:	push	rbp
0x10a82d:	push	rbx
0x10a82e:	sub	rsp, 0x38
0x10a832:	mov	ebx, dword ptr [rip + 0x20160]
0x10a838:	imul	ebx, d

0x10cf44:	mov	rax, qword ptr [rip + 0x1e4bd]
0x10cf4b:	mov	rdx, qword ptr [rax + 0x18]
0x10cf4f:	cmp	rdx, rbx
0x10cf52:	jae	0x10cf65
0x10cf54:	lea	rcx, [rdx + rbx]
0x10cf58:	sub	rcx, rbp
0x10cf5b:	cmp	rbx, rbp
0x10cf5e:	cmovae	rdx, rcx
0x10cf62:	mov	rbx, rdx
0x10cf65:	mov	qword ptr [rax + 0x20], rbx
0x10cf69:	mov	dword ptr [rax + 0x10], 0xa
0x10cf70:	add	rsp, 8
0x10cf74:	pop	rbx
0x10cf75:	pop	rbp
0x10cf76:	ret	
0x10cf65:	mov	qword ptr [rax + 0x20], rbx
0x10cf69:	mov	dword ptr [rax + 0x10], 0xa
0x10cf70:	add	rsp, 8
0x10cf74:	pop	rbx
0x10cf75:	pop	rbp
0x10cf76:	ret	
0x10cf77:	nop	word ptr [rax + rax]
0x10cf80:	endbr64	
0x10cf84:	push	rbp
0x10cf85:	push	rbx
0x10cf86:	sub	rsp, 8
0x10cf8a:	mov	rax, qword ptr [rip + 0x1e477]
0x10cf91:	mov	rbp, qword ptr [rax + 0x18]
0x10cf95:	mov	rbx, qword ptr [rax + 0x20]
0x10cf99:	mov	qword ptr [rax + 0x20], rbp
0x10cf9d:	xor	eax, eax
0x10cf9f:	call	0x10cb60
0x10cfa4:	xor	eax, eax
0x10cfa6:	mov	edi, 3
0x10cfab:	call	0x10c6e0
0x10cfb0:	mov	rax, qword ptr [

...

0x1155a4:	test	eax, eax
0x1155a6:	jne	0x1157c8
0x1155bd:	cmp	eax, -1
0x1155c0:	jne	0x1154c9
0x115715:	cmp	al, 0x79
0x115717:	je	0x1154b8
0x1156a4:	cmp	byte ptr [rbx + 0x6d], 0
0x1156a8:	je	0x1156b4
0x1157c8:	xor	eax, eax
0x1157ca:	mov	ecx, 0x12
0x1157cf:	mov	rsi, r12
0x1157d2:	lea	rdx, [rip + 0xad59]
0x1157d9:	lea	rdi, [rip + 0xc4c0]
0x1157e0:	call	0x10f760
0x11571d:	jmp	0x1155c6
0x1156b4:	mov	rbx, qword ptr [rsp + 0x10]
0x1156b9:	xor	eax, eax
0x1156bb:	mov	rdi, rbx
0x1156be:	call	0x110240
0x1156aa:	mov	rdi, rbx
0x1156ad:	xor	eax, eax
0x1156af:	call	0x10ec50
0x1157e5:	cmp	al, 0x79
0x1157e7:	jne	0x1156f8
0x1156c3:	cmp	byte ptr [rbx + 0x6d], 0
0x1156c7:	je	0x115431
0x1157ed:	mov	rdi, r12
0x1157f0:	call	0x1049b0
0x1156cd:	add	rsp, 0x28
0x1156d1:	mov	rdi, rbx
0x1156d4:	xor	eax, eax
0x1156d6:	pop	rbx
0x1156d7:	pop	rbp
0x1156d8:	pop	r12
0x1156da:	pop	r13
0x1156dc:	pop	r14
0x1156de:	pop	r15
0x1156e0:	jmp	0x110d70
0x1157f5:	lea	rdi, [rax + 0x21]
0x1157f9:	call	0x11d670
0x1157fe:	mov	rdx, -1
0x

0x117fce:	call	0x10bd00
0x117fb0:	mov	rdi, qword ptr [rbx]
0x117fb3:	mov	ecx, 1
0x117fb8:	mov	edx, 1
0x117fbd:	mov	rsi, r12
0x117fc0:	call	0x117320
0x117fd3:	cmp	eax, -1
0x117fd6:	je	0x118008
0x118008:	mov	r9, qword ptr [rsp]
0x11800c:	mov	r8, qword ptr [rbx]
0x11800f:	mov	rdx, r14
0x118012:	mov	esi, 1
0x118017:	mov	rcx, qword ptr [rip + 0x128ca]
0x11801e:	mov	rdi, qword ptr [rip + 0x1285b]
0x118025:	xor	eax, eax
0x118027:	call	0x104e60
0x117fd8:	mov	dword ptr [rbp], eax
0x117fdb:	add	rbx, 8
0x117fdf:	add	rbp, 4
0x117fe3:	cmp	rbx, r13
0x117fe6:	jne	0x117fb0
0x11802c:	jmp	0x117fdb
0x118005:	nop	dword ptr [rax]
0x118033:	nop	word ptr cs:[rax + rax]
0x11803e:	nop	
0x118040:	endbr64	
0x118044:	push	r12
0x118046:	cmp	byte ptr [rdi], 0x2f
0x118049:	mov	r12, rdi
0x11804c:	lea	rax, [rdi + 1]
0x118050:	je	0x118061
0x118061:	movzx	edx, byte ptr [rax]
0x118064:	mov	rsi, rax
0x118067:	test	dl, dl
0x118069:	jne	0x11808c
0x118052:	lea	rdi, [rip + 0x9f26]
0x118059:	call	0x108b00
0x11806b:	jmp	0x1180f

0x119d65:	jne	0x119d48
0x119d80:	movsxd	rax, edx
0x119d83:	add	rax, r9
0x119d86:	mov	byte ptr [rax], 0
0x119d89:	mov	dword ptr [r8], edx
0x119d8c:	movzx	eax, byte ptr [r13]
0x119d91:	jmp	0x119cf5
0x119ca9:	nop	dword ptr [rax]
0x119d0f:	nop	
0x119d43:	nop	dword ptr [rax + rax]
0x119d79:	nop	dword ptr [rax]
0x119d96:	nop	word ptr cs:[rax + rax]
0x119dda:	nop	word ptr [rax + rax]
0x119de0:	push	r15
0x119de2:	push	r14
0x119de4:	push	r13
0x119de6:	push	r12
0x119de8:	push	rbp
0x119de9:	push	rbx
0x119dea:	sub	rsp, 0x28
0x119dee:	mov	eax, dword ptr [rip + 0x11cf0]
0x119df4:	mov	ebx, dword ptr [rip + 0x11d02]
0x119dfa:	mov	dword ptr [rsp + 8], esi
0x119dfe:	mov	dword ptr [rsp + 0x18], edx
0x119e02:	mov	dword ptr [rsp + 0x1c], eax
0x119e06:	test	eax, eax
0x119e08:	je	0x119f9d
0x119f9d:	mov	r15d, 0xffffffff
0x119fa3:	jmp	0x119ecd
0x119e0e:	mov	rbp, rdi
0x119e11:	cmp	eax, ebx
0x119e13:	je	0x119fb0
0x119ecd:	add	rsp, 0x28
0x119ed1:	mov	eax, r15d
0x119ed4:	pop	rbx
0x119ed5:	pop	rbp
0x119ed6:	pop	r12

0x11c034:	mov	rsi, r13
0x11c037:	mov	rdi, rax
0x11c03a:	call	0x1048b0
0x11c290:	sub	eax, 0x30
0x11c293:	lea	ecx, [rsi + rsi*4]
0x11c296:	mov	r8d, edx
0x11c299:	movsx	eax, al
0x11c29c:	lea	esi, [rax + rcx*2]
0x11c29f:	movzx	eax, byte ptr [rbp + rdx]
0x11c2a4:	add	rdx, 1
0x11c2a8:	lea	ecx, [rax - 0x30]
0x11c2ab:	cmp	cl, 9
0x11c2ae:	jbe	0x11c290
0x11c2b0:	cmp	esi, 0x24
0x11c2b3:	sete	al
0x11c2b6:	cmp	esi, edi
0x11c2b8:	setge	dl
0x11c2bb:	or	eax, edx
0x11c2bd:	mov	dword ptr [rsp + 0x6c], r8d
0x11c2c2:	test	al, al
0x11c2c4:	je	0x11bdb3
0x11c3e5:	add	edx, 2
0x11c3e8:	mov	esi, 0x24
0x11c3ed:	mov	dword ptr [rsp + 0x6c], edx
0x11c3f1:	jmp	0x11bd98
0x11c122:	mov	dword ptr [rsp + 0x6c], r8d
0x11c127:	test	al, al
0x11c129:	je	0x11c3f6
0x11bf80:	add	edx, 1
0x11bf83:	mov	esi, 0x24
0x11bf88:	mov	edi, 0x24
0x11bf8d:	xor	eax, eax
0x11bf8f:	mov	dword ptr [rsp + 0x6c], edx
0x11bf93:	mov	rdx, r14
0x11bf96:	call	0x11b420
0x11b8fd:	cmp	al, 0x2a
0x11b8ff:	jne	0x11bd54
0x11bd4c:	cmp	al, 0x2f
0x11bd4e:	jg	0x11

0x11da58:	mov	rax, rbx
0x11da5b:	mul	rcx
0x11da5e:	mov	rbx, rax
0x11da61:	jo	0x11dc1d
0x11d9fd:	mov	rbx, rax
0x11da00:	jmp	0x11d9d7
0x11d9d4:	or	ebp, r8d
0x11d9d7:	add	rsi, r13
0x11d9da:	mov	eax, ebp
0x11d9dc:	or	eax, 2
0x11d9df:	mov	qword ptr [r15], rsi
0x11d9e2:	cmp	byte ptr [rsi], 0
0x11d9e5:	cmovne	ebp, eax
0x11d9e8:	jmp	0x11d893
0x11d9c0:	mov	rax, rbx
0x11d9c3:	mul	rcx
0x11d9c6:	mov	rbx, rax
0x11d9c9:	jo	0x11dc0e
0x11da94:	jmp	0x11d9d4
0x11da80:	mov	rax, rbx
0x11da83:	mul	rcx
0x11da86:	mov	rbx, rax
0x11da89:	jo	0x11dc2c
0x11dad4:	jmp	0x11d9d4
0x11dac0:	mov	rax, rbx
0x11dac3:	mul	rcx
0x11dac6:	mov	rbx, rax
0x11dac9:	jo	0x11dc3b
0x11d93d:	lea	rcx, [rip + 0x4c0c]
0x11d944:	movzx	edx, dl
0x11d947:	movsxd	rax, dword ptr [rcx + rdx*4]
0x11d94b:	add	rax, rcx
0x11d94e:	jmp	rax
0x11da41:	mov	rbx, rax
0x11da44:	xor	eax, eax
0x11da46:	or	ebp, eax
0x11da48:	jmp	0x11d9d7
0x11dbc0:	mov	esi, 1
0x11dbc5:	jmp	0x11daf0
0x11dba2:	mov	esi, 1
0x11dba7:	jmp	0x11da9c
0x11db84:	mov	esi, 1
0x11db89:	mov	e